In [1]:
import pandas as pd
import json
import numpy as np
import matplotlib.pyplot as plt

%load_ext autoreload
%autoreload 2
import sys
import os
sys.path.insert(0, '../')
from scripts.tracking import MatchTracking 
from scripts.pass_events import PassEvents
from scripts.ball_visualization import BallVisualization

In [32]:
data_directory = r'..\data\tracking'
file = 'g2312213_SecondSpectrum_tracking-produced.jsonl'
match_tracking_path = os.path.join(data_directory, file)
match_tracking = MatchTracking(tracking_file_path=match_tracking_path)

In [33]:
match_tracking.HomeTracking.df_tracking

period  frameIdx  gameClock      wallClock   live lastTouch  optaId  \
0            1         0       0.00  1678024891160  False      home  192194   
0            1         0       0.00  1678024891160  False      home  174349   
0            1         0       0.00  1678024891160  False      home   96385   
0            1         0       0.00  1678024891160  False      home  242633   
0            1         0       0.00  1678024891160  False      home  186022   
...        ...       ...        ...            ...    ...       ...     ...   
146413       2    146413    3027.24  1678031671160  False      home  186022   
146413       2    146413    3027.24  1678031671160  False      home  191726   
146413       2    146413    3027.24  1678031671160  False      home   96535   
146413       2    146413    3027.24  1678031671160  False      home  457401   
146413       2    146413    3027.24  1678031671160  False      home  434287   

        jersey_number  speed      x      y  
0                  25   0.00 -10.83   0.11  
0                   9   0.00  -0.27 -18.48  
0                   7   0.00  -7.89   8.70  
0                  15   0.00 -18.41  16.13  
0                   1   0.00 -47.00  -0.04  
...               ...    ...    ...    ...  
146413              1   2.15  48.99   3.89  
146413             12   0.87  24.22  17.58  
146413              5   0.40  46.65  -8.92  
146413              8   1.89   6.34   8.94  
146413              4   0.30  27.10  33.22  

[1610554 rows x 11 columns]

In [36]:
data_directory = r'..\data\statsbomb'
file = 'ManCity_Tottenham_events.json'
events_path = os.path.join(data_directory, file)
pass_events = PassEvents(tracking_file_path=events_path)

In [39]:
df_pass = pass_events.df_pass_home
df_track = match_tracking.HomeTracking.df_tracking

In [40]:
df_pass.head()

period  gameClock            team.name  duration pass.end_location  \
17       1      9.938  Manchester City WFC  1.464006       [85.9, 4.0]   
20       1     15.731  Manchester City WFC  1.126784     [109.1, 32.5]   
29       1     24.847  Manchester City WFC  0.712117       [87.2, 3.5]   
32       1     28.340  Manchester City WFC  2.169653      [80.2, 36.4]   
35       1     31.723  Manchester City WFC  1.784411     [100.0, 68.8]   

   pass.outcome.name     x     y  player.id               player.name  \
17               NaN  17.8  25.3    62666.0   Ingrid Filippa Angeldal   
20               NaN  45.7  33.9    15555.0               Lauren Hemp   
29               NaN  33.9  39.9    10163.0  Leila Ouahabi El Ouahabi   
32               NaN  25.9  34.8    25632.0              Yui Hasegawa   
35               NaN  21.4  -6.6    32210.0     Laia Aleixandri López   

    pass.recipient.id    pass.recipient.name  player.jersey_nb  \
17            15555.0            Lauren Hemp                12   
20            25554.0    Khadija Monifa Shaw                11   
29            25632.0           Yui Hasegawa                15   
32            32210.0  Laia Aleixandri López                25   
35            15570.0            Chloe Kelly                 4   

    pass.recipient.jersey_nb  
17                      11.0  
20                      21.0  
29                      25.0  
32                       4.0  
35                       9.0

In [41]:
df_track.head()

period  frameIdx  gameClock      wallClock   live lastTouch  optaId  \
0       1         0        0.0  1678024891160  False      home  192194   
0       1         0        0.0  1678024891160  False      home  174349   
0       1         0        0.0  1678024891160  False      home   96385   
0       1         0        0.0  1678024891160  False      home  242633   
0       1         0        0.0  1678024891160  False      home  186022   

   jersey_number  speed      x      y  
0             25    0.0 -10.83   0.11  
0              9    0.0  -0.27 -18.48  
0              7    0.0  -7.89   8.70  
0             15    0.0 -18.41  16.13  
0              1    0.0 -47.00  -0.04

In [49]:
df_pass['player.jersey_nb'] = df_pass['player.jersey_nb'].astype('Int32')
df_track['jersey_number'] = df_track['jersey_number'].astype('Int32')
df_merge = pd.merge_asof(df_pass.sort_values('gameClock'),df_track.sort_values('gameClock'),on='gameClock',left_by=['period','player.jersey_nb'],right_by=['period','jersey_number'])

In [61]:
df_merge.loc[df_merge['period']==1,['x_x','y_x','x_y','y_y']].iloc[250:].head(50)

x_x   y_x    x_y    y_y
512 -41.1   5.9 -32.76   1.76
513 -25.9 -14.9 -19.86 -17.40
514 -37.3   2.1 -29.59  -1.16
515 -25.3  10.5 -18.27   4.88
516 -19.6 -18.6 -12.85 -17.08
517   1.0 -24.8   1.86 -21.29
518  16.2 -27.7  15.40 -30.82
519  14.0 -24.8  12.94 -25.15
520  52.6 -26.7  49.38 -21.14
521  60.0 -40.0  51.35 -33.55
522  16.8  12.1  15.05   9.90
523  37.9   1.0  34.00   0.20
524  51.2  20.2  44.61  17.27
525  30.6  30.8  28.12  26.96
526  24.6  27.2  23.66  20.60
527  14.7 -10.8  15.35 -11.79
528  26.3 -13.9  24.22 -16.27
529  24.2 -14.1  22.69 -20.61
530  13.8 -18.7  11.33 -21.07
531   1.0  -6.8   0.52  -3.01
532  10.4  22.5   9.52  14.33
533  17.6  35.5  15.00  29.92
536  16.9  37.9  15.03  31.89
538  10.0  35.0   6.39  31.97
540 -35.0  24.6 -28.08  13.12
541 -26.9  11.4 -20.96  -2.19
542 -25.7  20.9 -20.02   8.90
543 -18.8  14.2 -14.71   3.47
547 -16.7   5.2 -12.52  -4.27
550  -9.4   6.7  -7.74   3.38
551  24.4  17.6  24.62   9.52
552  26.3  21.8  25.56  15.32
553 -32.3   9.3 -27.64   0.65
554 -20.1  -0.9 -17.67  -1.19
555  28.4 -18.7  26.19 -23.66
556  49.5 -29.7  38.67 -28.67
561  60.0 -40.0  51.11 -33.37
562  31.1  16.3  26.13   7.42
563  18.3  14.0  14.24   5.92
575  20.4  36.4  19.01  29.76
578  60.0  39.9  52.62  33.24
579 -37.1  30.8 -32.83  25.58
580 -54.8   4.1 -46.93   2.33
582 -39.5 -24.3 -34.09 -25.32
583 -44.7 -11.5 -36.12 -12.23
584 -34.9  15.9 -27.66   5.64
585 -19.6  22.3 -16.10  16.56
586  -8.2  19.2  -6.20  12.56
587 -17.7  29.3 -13.50  27.08
588  -9.7  36.5  -5.99  33.14

In [9]:
BV = BallVisualization(match_tracking, pass_events, period = 1)

In [10]:
BV.df_merged.head(10)

gameClock         x         y  type    color
0      0.000  0.230000  0.190000  ball  #000000
1      0.040  0.710000  0.300000  ball  #000000
2      0.080  1.160000  0.360000  ball  #000000
3      0.120  1.610000  0.420000  ball  #000000
4      0.160  2.060000  0.500000  ball  #000000
4      0.194 -0.859211  0.091591  pass  #FFB600
5      0.200  2.500000  0.580000  ball  #000000
6      0.240  2.940000  0.660000  ball  #000000
7      0.280  3.370000  0.740000  ball  #000000
8      0.320  3.790000  0.830000  ball  #000000

In [11]:
BV.lag_pass(0.1)

In [12]:
BV.df_merged.head(10)

gameClock         x         y  type    color
0      0.000  0.230000  0.190000  ball  #000000
1      0.040  0.710000  0.300000  ball  #000000
2      0.080  1.160000  0.360000  ball  #000000
3      0.120  1.610000  0.420000  ball  #000000
4      0.160  2.060000  0.500000  ball  #000000
5      0.200  2.500000  0.580000  ball  #000000
6      0.240  2.940000  0.660000  ball  #000000
7      0.280  3.370000  0.740000  ball  #000000
4      0.294 -0.859211  0.091591  pass  #FFB600
8      0.320  3.790000  0.830000  ball  #000000

In [20]:
BV.reset_lag()
BV.df_merged.head(10)

gameClock         x         y  type    color
0      0.000  0.230000  0.190000  ball  #000000
1      0.040  0.710000  0.300000  ball  #000000
2      0.080  1.160000  0.360000  ball  #000000
3      0.120  1.610000  0.420000  ball  #000000
4      0.160  2.060000  0.500000  ball  #000000
4      0.194 -0.859211  0.091591  pass  #FFB600
5      0.200  2.500000  0.580000  ball  #000000
6      0.240  2.940000  0.660000  ball  #000000
7      0.280  3.370000  0.740000  ball  #000000
8      0.320  3.790000  0.830000  ball  #000000

In [17]:
BV.plot(start = 1000, end = 1010, plot_step = 0.04)

In [21]:
BV.lag_pass(-0.3)

In [22]:
BV.plot(start = 1000, end = 1010, plot_step = 0.04)